Recently Google AI Research published a paper titled “EfficientNet: Rethinking Model Scaling for Convolutional Neural Networks”. In this paper the authors propose a new architecture which achieves state of the art classification accuracy on ImageNet while being 8.4x smaller and 6.1x faster on inference than the best existing CNN.
It achieves high level of acacuracy on many other datasets like CIFAR-100, Flowers and Cars. Good results on multiple dataset shows that the architecture can be used for transfer learning. 

In this notebook, I try to compare the proposed efficient models EB0 to EB5. The pretrained model weights on imagenet dataset of EB6 and EB7 haven't been released yet. I use [GradCam](https://arxiv.org/abs/1610.02391) to highlight what different models are looking at.

You can find a very nice implementation of GradCam [here](https://github.com/FrancescoSaverioZuppichini/A-journey-into-Convolutional-Neural-Network-visualization-). I use the pretrained model weights provided [here](https://github.com/lukemelas/EfficientNet-PyTorch#loading-pretrained-models) for visualization.

# About EfficientNet


A naive way to increase the performance of neural networks is to increase make CNN deeper. A great example, would be resnet ehich has several variations ranging from 18 to 202. Making the CNN deeper or wider may increase the performance but it comes at great computational cost. So we need some way to balance our ever increasing quest for performance with compuatational cost. In the paper, the authors propose a new model scaling method that uses a simple compound coefficient to scale up CNNs in a more structured manner. This method helps them to decide when to increase the depth or width of the network.

The authors wanted to optimize for accuracy and efficieny. So, they performed a neural architecture search. This search yielded th Efficient-B0 archictecture which looks pretty simple and straightforward to implement.

![EfficientNet-B0 Architecture](https://1.bp.blogspot.com/-DjZT_TLYZok/XO3BYqpxCJI/AAAAAAAAEKM/BvV53klXaTUuQHCkOXZZGywRMdU9v9T_wCLcBGAs/s640/image2.png)

As you can see from the performance graph, EfficientNet uses fewer parameters and achieves very high accuracy. For more details please [refer](https://arxiv.org/abs/1905.11946)

![Effiecient Performance](https://1.bp.blogspot.com/-oNSfIOzO8ko/XO3BtHnUx0I/AAAAAAAAEKk/rJ2tHovGkzsyZnCbwVad-Q3ZBnwQmCFsgCEwYBhgL/s640/image3.png)

# Installing dependencies

In [1]:
!git clone https://github.com/FrancescoSaverioZuppichini/A-journey-into-Convolutional-Neural-Network-visualization-.git
!pip install efficientnet_pytorch==0.2.0

Cloning into 'A-journey-into-Convolutional-Neural-Network-visualization-'...
remote: Enumerating objects: 49, done.
remote: Counting objects: 100% (49/49), done.
remote: Compressing objects: 100% (37/37), done.
remote: Total 238 (delta 12), reused 49 (delta 12), pack-reused 189
Receiving objects: 100% (238/238), 106.41 MiB | 49.05 MiB/s, done.
Resolving deltas: 100% (70/70), done.
  Stored in directory: /tmp/.cache/pip/wheels/85/20/c7/6d529b628dd965b5cfdba09b3544408c6d3f34a479453d0fe3
Successfully built efficientnet-pytorch


In [2]:
cd A-journey-into-Convolutional-Neural-Network-visualization-/

/kaggle/working/A-journey-into-Convolutional-Neural-Network-visualization-


# Import Packages

In [3]:
from torchvision.models import *
from visualisation.core.utils import device
from efficientnet_pytorch import EfficientNet
import glob
import matplotlib.pyplot as plt
import numpy as np
import torch 
from utils import *
import PIL.Image
import cv2

from visualisation.core.utils import device 
from visualisation.core.utils import image_net_postprocessing

from torchvision.transforms import ToTensor, Resize, Compose, ToPILImage
from visualisation.core import *
from visualisation.core.utils import image_net_preprocessing

# for animation
%matplotlib inline
from IPython.display import Image
from matplotlib.animation import FuncAnimation
from collections import OrderedDict

# Loading Test Images
I will be using images from Caltech 256 Image dataset. It has images from 257 different categories. Each category has around 120 images. I will be using images from some interesting categories. you can easily choose other categories for visualization if you want.

In [4]:
max_img = 5
path = '/kaggle/input/caltech256/256_objectcategories/256_ObjectCategories/'
interesting_categories = ['009.bear','038.chimp','251.airplanes-101','158.penguin',
                          '190.snake/','024.butterfly','151.ostrich']

images = [] 
for category_name in interesting_categories:
    image_paths = glob.glob(f'{path}/{category_name}/*')
    category_images = list(map(lambda x: PIL.Image.open(x), image_paths[:max_img]))
    images.extend(category_images)

inputs  = [Compose([Resize((224,224)), ToTensor(), image_net_preprocessing])(x).unsqueeze(0) for x in images]  # add 1 dim for batch
inputs = [i.to(device) for i in inputs]

# CAM Visualization

In [5]:
model_outs = OrderedDict()
model_instances = [lambda i,pretrained:efficientnet(i,pretrained)]
    
model_names = ['EB' + str(i) for i in range(6)]

images = list(map(lambda x: cv2.resize(np.array(x),(224,224)),images)) # resize i/p img

for i,name in enumerate(model_names):
    module = EfficientNet.from_pretrained('efficientnet-b'+str(i)).to(device)
    module.eval()

    vis = GradCam(module, device)

    model_outs[name] = list(map(lambda x: tensor2img(vis(x, None,postprocessing=image_net_postprocessing)[0]), inputs))
    del module
    torch.cuda.empty_cache()

Downloading: "http://storage.googleapis.com/public-models/efficientnet-b0-08094119.pth" to /tmp/.cache/torch/checkpoints/efficientnet-b0-08094119.pth
100%|██████████| 21383481/21383481 [00:00<00:00, 101138850.27it/s]


Loaded pretrained weights for efficientnet-b0


Downloading: "http://storage.googleapis.com/public-models/efficientnet-b1-dbc7070a.pth" to /tmp/.cache/torch/checkpoints/efficientnet-b1-dbc7070a.pth
100%|██████████| 31512055/31512055 [00:00<00:00, 109921398.46it/s]


Loaded pretrained weights for efficientnet-b1


Downloading: "http://storage.googleapis.com/public-models/efficientnet-b2-27687264.pth" to /tmp/.cache/torch/checkpoints/efficientnet-b2-27687264.pth
100%|██████████| 36797453/36797453 [00:00<00:00, 92416549.69it/s]


...

Loaded pretrained weights for efficientnet-b3


Downloading: "http://storage.googleapis.com/public-models/efficientnet-b4-e116e8b3.pth" to /tmp/.cache/torch/checkpoints/efficientnet-b4-e116e8b3.pth
100%|██████████| 77989391/77989391 [00:00<00:00, 120268550.59it/s]


Loaded pretrained weights for efficientnet-b4


Downloading: "http://storage.googleapis.com/public-models/efficientnet-b5-586e6cc6.pth" to /tmp/.cache/torch/checkpoints/efficientnet-b5-586e6cc6.pth
100%|██████████| 122398170/122398170 [00:00<00:00, 128136842.51it/s]


Loaded pretrained weights for efficientnet-b5


# Animating CAM

In [6]:
%%capture

# create a figure with two subplots
fig, (ax1, ax2, ax3, ax4, ax5, ax6,ax7) = plt.subplots(1,7,figsize=(20,20))
axes = [ax2, ax3, ax4, ax5, ax6, ax7]
    
def update(frame):
    all_ax = []
    ax1.set_yticklabels([])
    ax1.set_xticklabels([])
    ax1.text(1, 1, 'Orig. Im', color="white", ha="left", va="top",fontsize=30)
    all_ax.append(ax1.imshow(images[frame]))
    for i,(ax,name) in enumerate(zip(axes,model_outs.keys())):
        ax.set_yticklabels([])
        ax.set_xticklabels([])        
        ax.text(1, 1, name, color="white", ha="left", va="top",fontsize=20)
        all_ax.append(ax.imshow(model_outs[name][frame], animated=True))

    return all_ax

ani = FuncAnimation(fig, update, frames=range(len(images)), interval=1000, blit=True)
model_names = [m.__name__ for m in model_instances]
model_names = ', '.join(model_names)
fig.tight_layout()
ani.save('../compare_arch.gif', writer='imagemagick') 

In [7]:
Image('../compare_arch.gif')

In [8]:
cd ..

/kaggle/working


In [9]:
!rm -rf A-journey-into-Convolutional-Neural-Network-visualization-/